TODO: FacetGrid Multiple model density, velocity, accumulated sediment DynamicMaps

In [49]:
import xarray as xr
import hvplot.xarray
from JulesD3D.utils import quickDF
from JulesD3D.cleanNetCDF import fixMeshGrid, makeVelocity, addDepth, addUnderlayerCoords, makeBottomStress
import holoviews as hv
# import numpy as np
# import datashader as ds
# from holoviews import Layout
%load_ext autoreload

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Manually define the models

In [50]:
models = [
    {
        "filepath": "/Users/julesblom/ThesisResults/trim-36km_200m_W60ChannelRun01C.nc",
        "name":"Run 01"
    },    
    {
        "filepath": "/Users/julesblom/ThesisResults/trim-36km_200m_W60ChannelRun05C.nc",
        "name": "Run 05"
    },
    {
        "filepath": "/Users/julesblom/ThesisResults/trim-36km_200m_W60ChannelRun09C.nc",
        "name": "Run 09"
    },
]

### Or read all netCDF in a folder

In [3]:
trim_run1 = xr.open_dataset(models[0]['filepath'])

In [4]:
trim_run1.DPS.isel(time=0)

<xarray.DataArray 'DPS' (M: 132, N: 182)>
array([[  0.     ,   0.     ,   0.     , ...,   0.     ,   0.     ,   0.     ],
       [  0.     ,   0.     ,   0.     , ..., 699.20905, 699.90717, 699.90717],
       [  0.     ,   0.     ,   0.     , ..., 699.20905, 699.90717, 699.90717],
       ...,
       [  0.     ,   0.     ,   0.     , ..., 699.20905, 699.90717, 699.90717],
       [  0.     ,   0.     ,   0.     , ..., 699.20905, 699.90717, 699.90717],
       [  0.     ,   0.     ,   0.     , ...,   0.     ,   0.     ,   0.     ]],
      dtype=float32)
Coordinates:
    XZ       (M, N) float64 ...
    YZ       (M, N) float64 ...
    time     datetime64[ns] 2020-02-01
Dimensions without coordinates: M, N
Attributes:
    long_name:  Bottom depth (zeta point)
    units:      m
    grid:       grid
    location:   face

In [5]:
# array of xarray
trims = [xr.open_dataset(model_dict['filepath']) for model_dict in models]

In [32]:
channel_index = int(trim.M.size/2)

# Compare depth profile lineplots

In [36]:
depth_clim = (-1.0, 1.0)
end_profile_datasets_per_run = []
end_profile_datasets_total = []

In [7]:
# Ensure that datasets have equal startdates, this is hack for comparing in lineplot with hvplot
same_time = trims[0].time

In [35]:
# difference PER RUN
for (i, trim) in enumerate(trims):
    keyword = f"{models[i]['name']}" #_diff
    trim[keyword] = trim.DPS.isel(time=0) - trim.DPS
    
    diff_channel_end = trim[keyword]
    diff_channel_end['time'] = same_time # this is hack for comparing in lineplot with hvplot
    end_profile_datasets_per_run.append(diff_channel_end)

In [ ]:
merged_diff_per_run = xr.merge(end_profile_datasets_per_run, compat='override')
merged_diff_per_run = fixMeshGrid(merged_diff_per_run, merged_diff_per_run.XZ.values, merged_diff_per_run.YZ.values, mystery_flag=True)

In [19]:
merged_diff_per_run.isel(M=channel_index).hvplot.line(groupby='time', ylim=depth_clim)

NameError: name 'merged_diff_per_run' is not defined

## Total accumulated sediment over runs

In [37]:
# difference total
for (i, trim) in enumerate(trims):
    keyword = f"{models[i]['name']}_diff"
    trim[keyword] = trim_run1.DPS.isel(time=0) - trim.DPS
    
    diff_channel_end = trim[keyword]
    diff_channel_end['time'] = same_time # this is hack for comparing in lineplot with hvplot
    end_profile_datasets_total.append(diff_channel_end)

In [38]:
merged_bottom_diff_total = xr.merge(end_profile_datasets_total, compat='override')

In [39]:
merged_bottom_diff_total

<xarray.Dataset>
Dimensions:      (M: 132, N: 182, time: 11)
Coordinates:
    XZ           (M, N) float64 ...
    YZ           (M, N) float64 ...
  * time         (time) datetime64[ns] 2020-02-01 ... 2020-02-01T17:00:00
Dimensions without coordinates: M, N
Data variables:
    Run 01_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0
    Run 05_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0
    Run 09_diff  (M, N, time) float32 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0

In [40]:
# fix delft3d shitty outputes meshgrid with missing values
merged_bottom_diff_total = fixMeshGrid(merged_bottom_diff_total,
                                       merged_bottom_diff_total.XZ.values, merged_bottom_diff_total.YZ.values,
                                       mystery_flag=True)

Fixing mesh grid, assuming a uniform grid
x_gridstep 200.0
y_gridstep 200.0
width 26000.0
length 36200.0
132 x 182 grid
original XZ (132, 182)
original YZ (132, 182)
new XZ (132, 182)
new YZ (132, 182)


In [41]:
merged_bottom_diff_total_end = merged_bottom_diff_total.isel(time=-1)

In [45]:
map_clim = (-0.3, 0.3)

In [46]:
all_end_plots = [merged_bottom_diff_total_end[model_name].hvplot.quadmesh('XZ', 'YZ',cmap='PiYG', height=550, width=400, clabel='m', clim=map_clim, title=model_name) for model_name in ayehmm.data_vars]

In [47]:
all_end_plots[0] + all_end_plots[1] + all_end_plots[2]

:Layout
   .QuadMesh.I   :QuadMesh   [XZ,YZ]   (Run 01_diff)
   .QuadMesh.II  :QuadMesh   [XZ,YZ]   (Run 05_diff)
   .QuadMesh.III :QuadMesh   [XZ,YZ]   (Run 09_diff)

In [ ]:
# all_end_plots[3] + all_end_plots[4] 

In [ ]:
# all_end_plots[5] + all_end_plots[6]

In [48]:
merged_bottom_diff_total.isel(M=channel_index).hvplot.line(groupby='time', ylim=depth_clim)

:DynamicMap   [time]
   :NdOverlay   [Variable]
      :Curve   [YZ]   (value)